This notebook will demonstrate feature engineering and augmentation for the GRU/LSTM model.

GRU/LSTM part is mainly based on [OpenVaccine: Simple GRU Model](https://www.kaggle.com/xhlulu/openvaccine-simple-gru-model).


In [12]:
import pandas as pd
import numpy as np
import json
import tensorflow.keras.layers as L
import keras.backend as K
import tensorflow as tf
import plotly.express as px
from sklearn.model_selection import StratifiedKFold, KFold, GroupKFold
from sklearn.cluster import KMeans
import os

os.environ['CUDA_VISIBLE_DEVICES'] = '0'
def allocate_gpu_memory(gpu_number=0):
    physical_devices = tf.config.experimental.list_physical_devices('GPU')

    if physical_devices:
        try:
            print("Found {} GPU(s)".format(len(physical_devices)))
            tf.config.set_visible_devices(physical_devices[gpu_number], 'GPU')
            tf.config.experimental.set_memory_growth(physical_devices[gpu_number], True)
            print("#{} GPU memory is allocated".format(gpu_number))
        except RuntimeError as e:
            print(e)
    else:
        print("Not enough GPU hardware devices available")
allocate_gpu_memory()

Ver='GRU_LSTM1'
aug_data = '../input/openvaccine-augmentation-data/aug_data1.csv'
debug = False

Found 1 GPU(s)
#0 GPU memory is allocated


In [13]:
def gru_layer(hidden_dim, dropout):
    return L.Bidirectional(L.GRU(hidden_dim, dropout=dropout, return_sequences=True, kernel_initializer = 'orthogonal'))

def lstm_layer(hidden_dim, dropout):
    return L.Bidirectional(L.LSTM(hidden_dim, dropout=dropout, return_sequences=True, kernel_initializer = 'orthogonal'))

def build_model(seq_len=107, pred_len=68, dropout=0.5, embed_dim=100, hidden_dim=256, type=0):
    inputs = L.Input(shape=(seq_len, 6))
    
    # split categorical and numerical features and concatenate them later.
    categorical_feat_dim = 3
    categorical_fea = inputs[:, :, :categorical_feat_dim]
    numerical_fea = inputs[:, :, 3:]

    embed = L.Embedding(input_dim=len(token2int), output_dim=embed_dim)(categorical_fea)
    reshaped = tf.reshape(embed, shape=(-1, embed.shape[1],  embed.shape[2] * embed.shape[3]))
    reshaped = L.concatenate([reshaped, numerical_fea], axis=2)
    
    if type == 0:
        hidden = gru_layer(hidden_dim, dropout)(reshaped)
        hidden = gru_layer(hidden_dim, dropout)(hidden)
        hidden = gru_layer(hidden_dim, dropout)(hidden)
    elif type == 1:
        hidden = gru_layer(hidden_dim, dropout)(reshaped)
        hidden = gru_layer(hidden_dim, dropout)(hidden)
        hidden = lstm_layer(hidden_dim, dropout)(hidden)
    #elif type == 2:
    #    hidden = gru_layer(hidden_dim, dropout)(reshaped)
    #    hidden = lstm_layer(hidden_dim, dropout)(hidden)
    #    hidden = gru_layer(hidden_dim, dropout)(hidden)
    elif type == 2:
        hidden = lstm_layer(hidden_dim, dropout)(reshaped)
        hidden = lstm_layer(hidden_dim, dropout)(hidden)
        hidden = lstm_layer(hidden_dim, dropout)(hidden)
    
    truncated = hidden[:, :pred_len]
    out = L.Dense(5, activation='linear')(truncated)
    model = tf.keras.Model(inputs=inputs, outputs=out)
    model.compile(tf.keras.optimizers.Adam(), loss=mcrmse)
    return model

In [14]:
token2int = {x:i for i, x in enumerate('().ACGUBEHIMSX')}
pred_cols = ['reactivity', 'deg_Mg_pH10', 'deg_pH10', 'deg_Mg_50C', 'deg_50C']

def preprocess_inputs(df, cols=['sequence', 'structure', 'predicted_loop_type']):
    base_fea = np.transpose(
        np.array(
            df[cols]
            .applymap(lambda seq: [token2int[x] for x in seq])
            .values
            .tolist()
        ),
        (0, 2, 1)
    )
    bpps_sum_fea = np.array(df['bpps_sum'].to_list())[:,:,np.newaxis]
    bpps_max_fea = np.array(df['bpps_max'].to_list())[:,:,np.newaxis]
    bpps_nb_fea = np.array(df['bpps_nb'].to_list())[:,:,np.newaxis]
    return np.concatenate([base_fea,bpps_sum_fea,bpps_max_fea,bpps_nb_fea], 2)

def rmse(y_actual, y_pred):
    mse = tf.keras.losses.mean_squared_error(y_actual, y_pred)
    return K.sqrt(mse)

def mcrmse(y_actual, y_pred, num_scored=len(pred_cols)):
    score = 0
    for i in range(num_scored):
        score += rmse(y_actual[:, :, i], y_pred[:, :, i]) / num_scored
    return score

## Load and preprocess data

In [15]:
train = pd.read_json('../input/stanford-covid-vaccine/train.json', lines=True)
test = pd.read_json('../input/stanford-covid-vaccine/test.json', lines=True)

In [16]:
# additional features

def read_bpps_sum(df):
    bpps_arr = []
    for mol_id in df.id.to_list():
        bpps_arr.append(np.load(f"../input/stanford-covid-vaccine/bpps/{mol_id}.npy").max(axis=1))
    return bpps_arr

def read_bpps_max(df):
    bpps_arr = []
    for mol_id in df.id.to_list():
        bpps_arr.append(np.load(f"../input/stanford-covid-vaccine/bpps/{mol_id}.npy").sum(axis=1))
    return bpps_arr

def read_bpps_nb(df):
    # normalized non-zero number
    # from https://www.kaggle.com/symyksr/openvaccine-deepergcn 
    bpps_nb_mean = 0.077522 # mean of bpps_nb across all training data
    bpps_nb_std = 0.08914   # std of bpps_nb across all training data
    bpps_arr = []
    for mol_id in df.id.to_list():
        bpps = np.load(f"../input/stanford-covid-vaccine/bpps/{mol_id}.npy")
        bpps_nb = (bpps > 0).sum(axis=0) / bpps.shape[0]
        bpps_nb = (bpps_nb - bpps_nb_mean) / bpps_nb_std
        bpps_arr.append(bpps_nb)
    return bpps_arr 

train['bpps_sum'] = read_bpps_sum(train)
test['bpps_sum'] = read_bpps_sum(test)
train['bpps_max'] = read_bpps_max(train)
test['bpps_max'] = read_bpps_max(test)
train['bpps_nb'] = read_bpps_nb(train)
test['bpps_nb'] = read_bpps_nb(test)

In [17]:
# clustering for GroupKFold
# expecting more accurate CV by putting similar RNAs into the same fold.
kmeans_model = KMeans(n_clusters=200, random_state=110).fit(preprocess_inputs(train)[:,:,0])
train['cluster_id'] = kmeans_model.labels_

## Data augmentation for training and TTA(test)

In [18]:
aug_data = '../input/openvaccineaugmentationdata/aug_data1.csv'
aug_df = pd.read_csv(aug_data)
display(aug_df.head())

id                                           sequence  \
0  id_fff546103  GGAAAGCUAGGACGUGGGAGCGUAGCUCUCCACACGGGUACGCCAA...   
1  id_18ff9d670  GGAAAGAGCUCGUGAGAAGAAUCUAGUACAUGCAUACGCUACAUCU...   
2  id_177cd630b  GGAAAGAAGUAGCACGGUCCUAAGGUUACUGUAGCUAUGUCCAGCG...   
3  id_17a9ad5b7  GGAAAACACUGCAAAAGUCAACGAAGAAGUUGACUAAGAAGUGAUC...   
4  id_17ab91518  GGAAAACGCGCGCGCGCGCGCGCGCGCGCGCGCGCGCGCGCGCGCG...   

                                           structure  log_gamma     score  \
0  .....((((((((((((((((...)))).)))).((((((((((.....          2  0.981885   
1  .....(((.((.......((..((((.....((....)).....))...          0  0.887485   
2  (....((.((((((((((((...))..))))).))))).))(((.(...          2  0.923722   
3  ......((((((...(((((((......))))))).....((((((...          2  0.977602   
4  ......(((((((((((((((((((((((((((((....)))))))...          2  0.982851   

   cnt                                predicted_loop_type  
0    3  EEEEESSSSSSSSSSSSSSSSHHHSSSSBSSSSMSSSSSSSSSSHH...  
1    5  EEEEESSSISSIIIIIIISSIISSSSIIIIISSHHHHSSIIIIISS...  
2    3  SMMMMSSISSSSSSSSSSSSHHHSSBBSSSSSBSSSSSISSSSSIS...  
3    3  EEEEEESSSSSSMMMSSSSSSSHHHHHHSSSSSSSMMMMMSSSSSS...  
4    3  EEEEEESSSSSSSSSSSSSSSSSSSSSSSSSSSSSHHHHSSSSSSS...

This file was created using ARNIE, ViennaRNA and bpRNA in the following way.

Get candidate structures with different gamma values. 
See last cell of [How to Use ARNIE on Kaggle Notebook](https://www.kaggle.com/its7171/how-to-use-arnie-on-kaggle-notebook).

Remove the same as the original structure.

Get a structure with the largest score for each sequence.

Get the predicted_loop_type from the sequence and structure.
See [How to Generate predicted_loop_type](https://www.kaggle.com/its7171/how-to-generate-predicted-loop-type).

In [19]:
def aug_data(df):
    target_df = df.copy()
    new_df = aug_df[aug_df['id'].isin(target_df['id'])]
                         
    del target_df['structure']
    del target_df['predicted_loop_type']
    new_df = new_df.merge(target_df, on=['id','sequence'], how='left')

    df['cnt'] = df['id'].map(new_df[['id','cnt']].set_index('id').to_dict()['cnt'])
    df['log_gamma'] = 100
    df['score'] = 1.0
    df = df.append(new_df[df.columns])
    return df
train = aug_data(train)
test = aug_data(test)

In [20]:
if debug:
    train = train[:200]
    test = test[:200]

## Build and train model

In [21]:
model = build_model()
model.summary()

Model: "functional_3"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_2 (InputLayer)            [(None, 107, 6)]     0                                            
__________________________________________________________________________________________________
tf_op_layer_strided_slice_3 (Te [(None, 107, 3)]     0           input_2[0][0]                    
__________________________________________________________________________________________________
embedding_1 (Embedding)         (None, 107, 3, 100)  1400        tf_op_layer_strided_slice_3[0][0]
__________________________________________________________________________________________________
tf_op_layer_Reshape_1 (TensorFl [(None, 107, 300)]   0           embedding_1[0][0]                
_______________________________________________________________________________________

In [24]:
FOLD_N=5
gkf = GroupKFold(n_splits=FOLD_N)

type=1
for cv, (tr_idx, vl_idx) in enumerate(gkf.split(train,  train['reactivity'], train['cluster_id'])):
    trn = train.iloc[tr_idx]
    x_trn = preprocess_inputs(trn)
    y_trn = np.array(trn[pred_cols].values.tolist()).transpose((0, 2, 1))
    w_trn = np.log(trn.signal_to_noise+1.1)/2

    val = train.iloc[vl_idx]
    x_val_all = preprocess_inputs(val)
    val = val[val.SN_filter == 1]
    x_val = preprocess_inputs(val)
    y_val = np.array(val[pred_cols].values.tolist()).transpose((0, 2, 1))

    model = build_model(type=1)
    model_short = build_model(seq_len=107, pred_len=107,type=type)
    model_long = build_model(seq_len=130, pred_len=130,type=type)

    history = model.fit(
        x_trn, y_trn,
        validation_data = (x_val, y_val),
        batch_size=64,
        epochs=100,
        sample_weight=w_trn,
        callbacks=[
            tf.keras.callbacks.ReduceLROnPlateau(),
            tf.keras.callbacks.ModelCheckpoint(f'model{Ver}_cv{cv}.h5')
        ]
        )
    print(f"Min training loss={min(history.history['loss'])}, min validation loss={min(history.history['val_loss'])}")
    fig = px.line(history.history, y=['loss', 'val_loss'], labels={'index': 'epoch', 'value': 'Mean Cloumnwise Root Mean Squared Error'}, 
    title='Training History')
    fig.show()


Epoch 1/100
60/60 [==============================] - 7s 122ms/step - loss: 0.3317 - val_loss: 0.3577
Epoch 2/100
60/60 [==============================] - 6s 92ms/step - loss: 0.2780 - val_loss: 0.3087
Epoch 3/100
60/60 [==============================] - 6s 96ms/step - loss: 0.2575 - val_loss: 0.2892
Epoch 4/100
60/60 [==============================] - 6s 92ms/step - loss: 0.2428 - val_loss: 0.2712
Epoch 5/100
60/60 [==============================] - 6s 95ms/step - loss: 0.2293 - val_loss: 0.2608
Epoch 6/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2194 - val_loss: 0.2506
Epoch 7/100
60/60 [==============================] - 6s 95ms/step - loss: 0.2109 - val_loss: 0.2444
Epoch 8/100
60/60 [==============================] - 6s 92ms/step - loss: 0.2028 - val_loss: 0.2396
Epoch 9/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1973 - val_loss: 0.2335
Epoch 10/100
60/60 [==============================] - 6s 92ms/step - loss: 0.1923 - val_loss: 0.232

60/60 [==============================] - 6s 94ms/step - loss: 0.1366 - val_loss: 0.2265
Epoch 83/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1366 - val_loss: 0.2265
Epoch 84/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1366 - val_loss: 0.2265
Epoch 85/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1366 - val_loss: 0.2265
Epoch 86/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1366 - val_loss: 0.2265
Epoch 87/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1367 - val_loss: 0.2265
Epoch 88/100
60/60 [==============================] - 6s 92ms/step - loss: 0.1367 - val_loss: 0.2265
Epoch 89/100
60/60 [==============================] - 6s 97ms/step - loss: 0.1367 - val_loss: 0.2265
Epoch 90/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1365 - val_loss: 0.2265
Epoch 91/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1364 - val_loss: 0.2265
Epo

Epoch 1/100
60/60 [==============================] - 8s 131ms/step - loss: 0.3368 - val_loss: 0.3471
Epoch 2/100
60/60 [==============================] - 6s 92ms/step - loss: 0.2785 - val_loss: 0.3050
Epoch 3/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2566 - val_loss: 0.2910
Epoch 4/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2419 - val_loss: 0.2751
Epoch 5/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2304 - val_loss: 0.2648
Epoch 6/100
60/60 [==============================] - 6s 92ms/step - loss: 0.2176 - val_loss: 0.2532
Epoch 7/100
60/60 [==============================] - 6s 95ms/step - loss: 0.2085 - val_loss: 0.2511
Epoch 8/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2006 - val_loss: 0.2509
Epoch 9/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1944 - val_loss: 0.2435
Epoch 10/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1899 - val_loss: 0.237

60/60 [==============================] - 6s 93ms/step - loss: 0.1214 - val_loss: 0.2285
Epoch 83/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1216 - val_loss: 0.2285
Epoch 84/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1217 - val_loss: 0.2285
Epoch 85/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1215 - val_loss: 0.2285
Epoch 86/100
60/60 [==============================] - 6s 92ms/step - loss: 0.1216 - val_loss: 0.2285
Epoch 87/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1215 - val_loss: 0.2285
Epoch 88/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1216 - val_loss: 0.2285
Epoch 89/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1216 - val_loss: 0.2285
Epoch 90/100
60/60 [==============================] - 6s 92ms/step - loss: 0.1214 - val_loss: 0.2285
Epoch 91/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1216 - val_loss: 0.2285
Epo

Epoch 1/100
60/60 [==============================] - 7s 120ms/step - loss: 0.3326 - val_loss: 0.3451
Epoch 2/100
60/60 [==============================] - 6s 95ms/step - loss: 0.2799 - val_loss: 0.2991
Epoch 3/100
60/60 [==============================] - 6s 92ms/step - loss: 0.2557 - val_loss: 0.2922
Epoch 4/100
60/60 [==============================] - 6s 95ms/step - loss: 0.2409 - val_loss: 0.2698
Epoch 5/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2261 - val_loss: 0.2661
Epoch 6/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2143 - val_loss: 0.2557
Epoch 7/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2055 - val_loss: 0.2518
Epoch 8/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1987 - val_loss: 0.2449
Epoch 9/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1938 - val_loss: 0.2475
Epoch 10/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1885 - val_loss: 0.248

60/60 [==============================] - 6s 93ms/step - loss: 0.1291 - val_loss: 0.2417
Epoch 83/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1291 - val_loss: 0.2417
Epoch 84/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1289 - val_loss: 0.2417
Epoch 85/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1290 - val_loss: 0.2417
Epoch 86/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1291 - val_loss: 0.2417
Epoch 87/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1289 - val_loss: 0.2417
Epoch 88/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1292 - val_loss: 0.2417
Epoch 89/100
60/60 [==============================] - 6s 92ms/step - loss: 0.1290 - val_loss: 0.2417
Epoch 90/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1292 - val_loss: 0.2417
Epoch 91/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1292 - val_loss: 0.2417
Epo

Epoch 1/100
60/60 [==============================] - 7s 122ms/step - loss: 0.3362 - val_loss: 0.3550
Epoch 2/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2784 - val_loss: 0.3098
Epoch 3/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2564 - val_loss: 0.2862
Epoch 4/100
60/60 [==============================] - 5s 91ms/step - loss: 0.2419 - val_loss: 0.2697
Epoch 5/100
60/60 [==============================] - 6s 92ms/step - loss: 0.2290 - val_loss: 0.2588
Epoch 6/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2162 - val_loss: 0.2509
Epoch 7/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2061 - val_loss: 0.2424
Epoch 8/100
60/60 [==============================] - 5s 91ms/step - loss: 0.1995 - val_loss: 0.2464
Epoch 9/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1944 - val_loss: 0.2381
Epoch 10/100
60/60 [==============================] - 6s 92ms/step - loss: 0.1886 - val_loss: 0.238

60/60 [==============================] - 6s 92ms/step - loss: 0.1274 - val_loss: 0.2305
Epoch 83/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1274 - val_loss: 0.2305
Epoch 84/100
60/60 [==============================] - 5s 91ms/step - loss: 0.1275 - val_loss: 0.2305
Epoch 85/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1274 - val_loss: 0.2305
Epoch 86/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1275 - val_loss: 0.2305
Epoch 87/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1274 - val_loss: 0.2305
Epoch 88/100
60/60 [==============================] - 5s 91ms/step - loss: 0.1274 - val_loss: 0.2305
Epoch 89/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1275 - val_loss: 0.2305
Epoch 90/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1274 - val_loss: 0.2305
Epoch 91/100
60/60 [==============================] - 6s 92ms/step - loss: 0.1274 - val_loss: 0.2305
Epo

Epoch 1/100
60/60 [==============================] - 7s 122ms/step - loss: 0.3354 - val_loss: 0.3419
Epoch 2/100
60/60 [==============================] - 5s 91ms/step - loss: 0.2796 - val_loss: 0.2960
Epoch 3/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2583 - val_loss: 0.2751
Epoch 4/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2419 - val_loss: 0.2617
Epoch 5/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2270 - val_loss: 0.2490
Epoch 6/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2141 - val_loss: 0.2430
Epoch 7/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2044 - val_loss: 0.2363
Epoch 8/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1975 - val_loss: 0.2309
Epoch 9/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1919 - val_loss: 0.2308
Epoch 10/100
60/60 [==============================] - 6s 92ms/step - loss: 0.1872 - val_loss: 0.231

60/60 [==============================] - 5s 91ms/step - loss: 0.1312 - val_loss: 0.2220
Epoch 83/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1312 - val_loss: 0.2220
Epoch 84/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1312 - val_loss: 0.2220
Epoch 85/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1312 - val_loss: 0.2220
Epoch 86/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1312 - val_loss: 0.2220
Epoch 87/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1312 - val_loss: 0.2220
Epoch 88/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1312 - val_loss: 0.2220
Epoch 89/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1312 - val_loss: 0.2220
Epoch 90/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1313 - val_loss: 0.2220
Epoch 91/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1312 - val_loss: 0.2220
Epo

In [25]:
FOLD_N=5
gkf = GroupKFold(n_splits=FOLD_N)

type=0
for cv, (tr_idx, vl_idx) in enumerate(gkf.split(train,  train['reactivity'], train['cluster_id'])):
    trn = train.iloc[tr_idx]
    x_trn = preprocess_inputs(trn)
    y_trn = np.array(trn[pred_cols].values.tolist()).transpose((0, 2, 1))
    w_trn = np.log(trn.signal_to_noise+1.1)/2

    val = train.iloc[vl_idx]
    x_val_all = preprocess_inputs(val)
    val = val[val.SN_filter == 1]
    x_val = preprocess_inputs(val)
    y_val = np.array(val[pred_cols].values.tolist()).transpose((0, 2, 1))

    model = build_model(type=1)
    model_short = build_model(seq_len=107, pred_len=107,type=type)
    model_long = build_model(seq_len=130, pred_len=130,type=type)

    history = model.fit(
        x_trn, y_trn,
        validation_data = (x_val, y_val),
        batch_size=64,
        epochs=100,
        sample_weight=w_trn,
        callbacks=[
            tf.keras.callbacks.ReduceLROnPlateau(),
            tf.keras.callbacks.ModelCheckpoint(f'model{Ver}_cv{cv}.h5')
        ]
        )
    print(f"Min training loss={min(history.history['loss'])}, min validation loss={min(history.history['val_loss'])}")
    fig = px.line(history.history, y=['loss', 'val_loss'], labels={'index': 'epoch', 'value': 'Mean Cloumnwise Root Mean Squared Error'}, 
    title='Training History')
    fig.show()


Epoch 1/100
60/60 [==============================] - 7s 122ms/step - loss: 0.3426 - val_loss: 0.3616
Epoch 2/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2839 - val_loss: 0.3131
Epoch 3/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2593 - val_loss: 0.2995
Epoch 4/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2465 - val_loss: 0.2750
Epoch 5/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2322 - val_loss: 0.2608
Epoch 6/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2218 - val_loss: 0.2531
Epoch 7/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2134 - val_loss: 0.2443
Epoch 8/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2048 - val_loss: 0.2388
Epoch 9/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1994 - val_loss: 0.2366
Epoch 10/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1950 - val_loss: 0.233

60/60 [==============================] - 6s 94ms/step - loss: 0.1295 - val_loss: 0.2307
Epoch 83/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1296 - val_loss: 0.2307
Epoch 84/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1297 - val_loss: 0.2307
Epoch 85/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1296 - val_loss: 0.2307
Epoch 86/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1296 - val_loss: 0.2307
Epoch 87/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1296 - val_loss: 0.2307
Epoch 88/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1296 - val_loss: 0.2307
Epoch 89/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1294 - val_loss: 0.2307
Epoch 90/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1295 - val_loss: 0.2307
Epoch 91/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1295 - val_loss: 0.2307
Epo

Epoch 1/100
60/60 [==============================] - 7s 119ms/step - loss: 0.3375 - val_loss: 0.3478
Epoch 2/100
60/60 [==============================] - 5s 92ms/step - loss: 0.2770 - val_loss: 0.3055
Epoch 3/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2555 - val_loss: 0.2915
Epoch 4/100
60/60 [==============================] - 6s 92ms/step - loss: 0.2418 - val_loss: 0.2767
Epoch 5/100
60/60 [==============================] - 6s 92ms/step - loss: 0.2302 - val_loss: 0.2626
Epoch 6/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2178 - val_loss: 0.2546
Epoch 7/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2071 - val_loss: 0.2473
Epoch 8/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1989 - val_loss: 0.2440
Epoch 9/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1936 - val_loss: 0.2407
Epoch 10/100
60/60 [==============================] - 5s 92ms/step - loss: 0.1889 - val_loss: 0.239

60/60 [==============================] - 6s 94ms/step - loss: 0.1187 - val_loss: 0.2308
Epoch 83/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1187 - val_loss: 0.2308
Epoch 84/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1187 - val_loss: 0.2308
Epoch 85/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1187 - val_loss: 0.2308
Epoch 86/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1188 - val_loss: 0.2308
Epoch 87/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1188 - val_loss: 0.2308
Epoch 88/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1188 - val_loss: 0.2308
Epoch 89/100
60/60 [==============================] - 6s 92ms/step - loss: 0.1188 - val_loss: 0.2308
Epoch 90/100
60/60 [==============================] - 6s 92ms/step - loss: 0.1186 - val_loss: 0.2308
Epoch 91/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1186 - val_loss: 0.2308
Epo

Epoch 1/100
60/60 [==============================] - 8s 129ms/step - loss: 0.3350 - val_loss: 0.3390
Epoch 2/100
60/60 [==============================] - 5s 92ms/step - loss: 0.2788 - val_loss: 0.3018
Epoch 3/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2580 - val_loss: 0.2883
Epoch 4/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2429 - val_loss: 0.2743
Epoch 5/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2280 - val_loss: 0.2594
Epoch 6/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2157 - val_loss: 0.2531
Epoch 7/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2052 - val_loss: 0.2562
Epoch 8/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1994 - val_loss: 0.2502
Epoch 9/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1936 - val_loss: 0.2529
Epoch 10/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1887 - val_loss: 0.249

60/60 [==============================] - 6s 94ms/step - loss: 0.1376 - val_loss: 0.2433
Epoch 83/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1376 - val_loss: 0.2433
Epoch 84/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1375 - val_loss: 0.2433
Epoch 85/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1377 - val_loss: 0.2433
Epoch 86/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1375 - val_loss: 0.2433
Epoch 87/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1376 - val_loss: 0.2433
Epoch 88/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1376 - val_loss: 0.2433
Epoch 89/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1377 - val_loss: 0.2433
Epoch 90/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1376 - val_loss: 0.2433
Epoch 91/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1377 - val_loss: 0.2433
Epo

Epoch 1/100
60/60 [==============================] - 7s 122ms/step - loss: 0.3275 - val_loss: 0.3536
Epoch 2/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2768 - val_loss: 0.3058
Epoch 3/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2551 - val_loss: 0.2824
Epoch 4/100
60/60 [==============================] - 6s 95ms/step - loss: 0.2386 - val_loss: 0.2709
Epoch 5/100
60/60 [==============================] - 6s 92ms/step - loss: 0.2248 - val_loss: 0.2564
Epoch 6/100
60/60 [==============================] - 6s 95ms/step - loss: 0.2137 - val_loss: 0.2473
Epoch 7/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2045 - val_loss: 0.2433
Epoch 8/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1976 - val_loss: 0.2411
Epoch 9/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1925 - val_loss: 0.2358
Epoch 10/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1873 - val_loss: 0.236

60/60 [==============================] - 6s 95ms/step - loss: 0.1282 - val_loss: 0.2295
Epoch 83/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1282 - val_loss: 0.2295
Epoch 84/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1282 - val_loss: 0.2295
Epoch 85/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1282 - val_loss: 0.2295
Epoch 86/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1281 - val_loss: 0.2295
Epoch 87/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1282 - val_loss: 0.2295
Epoch 88/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1282 - val_loss: 0.2295
Epoch 89/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1281 - val_loss: 0.2295
Epoch 90/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1281 - val_loss: 0.2295
Epoch 91/100
60/60 [==============================] - 6s 93ms/step - loss: 0.1282 - val_loss: 0.2295
Epo

Epoch 1/100
60/60 [==============================] - 7s 123ms/step - loss: 0.3320 - val_loss: 0.3429
Epoch 2/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2816 - val_loss: 0.2953
Epoch 3/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2582 - val_loss: 0.2753
Epoch 4/100
60/60 [==============================] - 6s 93ms/step - loss: 0.2416 - val_loss: 0.2622
Epoch 5/100
60/60 [==============================] - 6s 95ms/step - loss: 0.2264 - val_loss: 0.2503
Epoch 6/100
60/60 [==============================] - 6s 98ms/step - loss: 0.2138 - val_loss: 0.2428
Epoch 7/100
60/60 [==============================] - 6s 94ms/step - loss: 0.2043 - val_loss: 0.2361
Epoch 8/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1974 - val_loss: 0.2306
Epoch 9/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1916 - val_loss: 0.2294
Epoch 10/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1878 - val_loss: 0.227

60/60 [==============================] - 6s 93ms/step - loss: 0.1272 - val_loss: 0.2220
Epoch 83/100
60/60 [==============================] - 6s 96ms/step - loss: 0.1271 - val_loss: 0.2220
Epoch 84/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1270 - val_loss: 0.2220
Epoch 85/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1273 - val_loss: 0.2220
Epoch 86/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1271 - val_loss: 0.2220
Epoch 87/100
60/60 [==============================] - 6s 95ms/step - loss: 0.1272 - val_loss: 0.2220
Epoch 88/100
60/60 [==============================] - 5s 91ms/step - loss: 0.1271 - val_loss: 0.2220
Epoch 89/100
60/60 [==============================] - 6s 100ms/step - loss: 0.1271 - val_loss: 0.2220
Epoch 90/100
60/60 [==============================] - 6s 96ms/step - loss: 0.1271 - val_loss: 0.2220
Epoch 91/100
60/60 [==============================] - 6s 94ms/step - loss: 0.1271 - val_loss: 0.2220
Ep

In [ ]:
FOLD_N=5
gkf = GroupKFold(n_splits=FOLD_N)

type=2
for cv, (tr_idx, vl_idx) in enumerate(gkf.split(train,  train['reactivity'], train['cluster_id'])):
    trn = train.iloc[tr_idx]
    x_trn = preprocess_inputs(trn)
    y_trn = np.array(trn[pred_cols].values.tolist()).transpose((0, 2, 1))
    w_trn = np.log(trn.signal_to_noise+1.1)/2

    val = train.iloc[vl_idx]
    x_val_all = preprocess_inputs(val)
    val = val[val.SN_filter == 1]
    x_val = preprocess_inputs(val)
    y_val = np.array(val[pred_cols].values.tolist()).transpose((0, 2, 1))

    model = build_model(type=1)
    model_short = build_model(seq_len=107, pred_len=107,type=type)
    model_long = build_model(seq_len=130, pred_len=130,type=type)

    history = model.fit(
        x_trn, y_trn,
        validation_data = (x_val, y_val),
        batch_size=64,
        epochs=100,
        sample_weight=w_trn,
        callbacks=[
            tf.keras.callbacks.ReduceLROnPlateau(),
            tf.keras.callbacks.ModelCheckpoint(f'model{Ver}_cv{cv}.h5')
        ]
        )
    print(f"Min training loss={min(history.history['loss'])}, min validation loss={min(history.history['val_loss'])}")
    fig = px.line(history.history, y=['loss', 'val_loss'], labels={'index': 'epoch', 'value': 'Mean Cloumnwise Root Mean Squared Error'}, 
    title='Training History')
    fig.show()


In [11]:
def train_and_predict(type = 0, FOLD_N = 5):
    
    gkf = GroupKFold(n_splits=FOLD_N)

    public_df = test.query("seq_length == 107").copy()
    private_df = test.query("seq_length == 130").copy()

    public_inputs = preprocess_inputs(public_df)
    private_inputs = preprocess_inputs(private_df)


    holdouts = []
    holdout_preds = []

    for cv, (tr_idx, vl_idx) in enumerate(gkf.split(train,  train['reactivity'], train['cluster_id'])):
        trn = train.iloc[tr_idx]
        x_trn = preprocess_inputs(trn)
        y_trn = np.array(trn[pred_cols].values.tolist()).transpose((0, 2, 1))
        w_trn = np.log(trn.signal_to_noise+1.1)/2

        val = train.iloc[vl_idx]
        x_val_all = preprocess_inputs(val)
        val = val[val.SN_filter == 1]
        x_val = preprocess_inputs(val)
        y_val = np.array(val[pred_cols].values.tolist()).transpose((0, 2, 1))

        model = build_model(type=type)
        model_short = build_model(seq_len=107, pred_len=107,type=type)
        model_long = build_model(seq_len=130, pred_len=130,type=type)

        history = model.fit(
            x_trn, y_trn,
            validation_data = (x_val, y_val),
            batch_size=64,
            epochs=100,
            sample_weight=w_trn,
            callbacks=[
                tf.keras.callbacks.ReduceLROnPlateau(),
                tf.keras.callbacks.ModelCheckpoint(f'model{Ver}_cv{cv}.h5')
            ]
        )

        fig = px.line(
            history.history, y=['loss', 'val_loss'], 
            labels={'index': 'epoch', 'value': 'Mean Squared Error'}, 
            title='Training History')
        fig.show()

        model.load_weights(f'model{Ver}_cv{cv}.h5')
        model_short.load_weights(f'model{Ver}_cv{cv}.h5')
        model_long.load_weights(f'model{Ver}_cv{cv}.h5')

        holdouts.append(train.iloc[vl_idx])
        holdout_preds.append(model.predict(x_val_all))
        if cv == 0:
            public_preds = model_short.predict(public_inputs)/FOLD_N
            private_preds = model_long.predict(private_inputs)/FOLD_N
        else:
            public_preds += model_short.predict(public_inputs)/FOLD_N
            private_preds += model_long.predict(private_inputs)/FOLD_N
    return holdouts, holdout_preds, public_df, public_preds, private_df, private_preds

In [12]:
val_df, val_preds, test_df, test_preds = [], [], [], []
if debug:
    nmodel = 1
else:
    nmodel = 3
for i in range(nmodel):
    holdouts, holdout_preds, public_df, public_preds, private_df, private_preds = train_and_predict(i)
    val_df += holdouts
    val_preds += holdout_preds
    test_df.append(public_df)
    test_df.append(private_df)
    test_preds.append(public_preds)
    test_preds.append(private_preds)

Epoch 1/100
60/60 [==============================] - 7s 119ms/step - loss: 0.3363 - val_loss: 0.3621
Epoch 2/100
60/60 [==============================] - 5s 89ms/step - loss: 0.2840 - val_loss: 0.3168
Epoch 3/100
60/60 [==============================] - 5s 88ms/step - loss: 0.2649 - val_loss: 0.3072
Epoch 4/100
60/60 [==============================] - 5s 88ms/step - loss: 0.2530 - val_loss: 0.2842
Epoch 5/100
60/60 [==============================] - 5s 89ms/step - loss: 0.2422 - val_loss: 0.2718
Epoch 6/100
60/60 [==============================] - 5s 88ms/step - loss: 0.2316 - val_loss: 0.2586
Epoch 7/100
60/60 [==============================] - 5s 89ms/step - loss: 0.2238 - val_loss: 0.2562
Epoch 8/100
60/60 [==============================] - 5s 88ms/step - loss: 0.2161 - val_loss: 0.2476
Epoch 9/100
60/60 [==============================] - 5s 88ms/step - loss: 0.2094 - val_loss: 0.2429
Epoch 10/100
60/60 [==============================] - 5s 89ms/step - loss: 0.2037 - val_loss: 0.237

60/60 [==============================] - 5s 90ms/step - loss: 0.1383 - val_loss: 0.2241
Epoch 83/100
60/60 [==============================] - 5s 89ms/step - loss: 0.1383 - val_loss: 0.2241
Epoch 84/100
60/60 [==============================] - 5s 88ms/step - loss: 0.1384 - val_loss: 0.2241
Epoch 85/100
60/60 [==============================] - 5s 89ms/step - loss: 0.1384 - val_loss: 0.2241
Epoch 86/100
60/60 [==============================] - 5s 88ms/step - loss: 0.1383 - val_loss: 0.2241
Epoch 87/100
60/60 [==============================] - 5s 88ms/step - loss: 0.1382 - val_loss: 0.2241
Epoch 88/100
60/60 [==============================] - 5s 90ms/step - loss: 0.1384 - val_loss: 0.2241
Epoch 89/100
60/60 [==============================] - 5s 89ms/step - loss: 0.1382 - val_loss: 0.2241
Epoch 90/100
60/60 [==============================] - 5s 89ms/step - loss: 0.1384 - val_loss: 0.2241
Epoch 91/100
60/60 [==============================] - 5s 89ms/step - loss: 0.1383 - val_loss: 0.2241
Epo

KeyboardInterrupt: 

## post process

In [ ]:
preds_ls = []
for df, preds in zip(test_df, test_preds):
    for i, uid in enumerate(df.id):
        single_pred = preds[i]
        single_df = pd.DataFrame(single_pred, columns=pred_cols)
        single_df['id_seqpos'] = [f'{uid}_{x}' for x in range(single_df.shape[0])]
        preds_ls.append(single_df)
preds_df = pd.concat(preds_ls).groupby('id_seqpos').mean().reset_index()
# .mean() is for
# 1, Predictions from multiple models
# 2, TTA (augmented test data)

preds_ls = []
for df, preds in zip(val_df, val_preds):
    for i, uid in enumerate(df.id):
        single_pred = preds[i]
        single_df = pd.DataFrame(single_pred, columns=pred_cols)
        single_df['id_seqpos'] = [f'{uid}_{x}' for x in range(single_df.shape[0])]
        single_df['SN_filter'] = df[df['id'] == uid].SN_filter.values[0]
        preds_ls.append(single_df)
holdouts_df = pd.concat(preds_ls).groupby('id_seqpos').mean().reset_index()

In [ ]:
submission = preds_df[['id_seqpos', 'reactivity', 'deg_Mg_pH10', 'deg_pH10', 'deg_Mg_50C', 'deg_50C']]
submission.to_csv(f'submission.csv', index=False)
print(f'wrote to submission.csv')

## Validation

In [ ]:
def print_mse(prd):
    val = pd.read_json('../input/stanford-covid-vaccine/train.json', lines=True)

    val_data = []
    for mol_id in val['id'].unique():
        sample_data = val.loc[val['id'] == mol_id]
        sample_seq_length = sample_data.seq_length.values[0]
        for i in range(68):
            sample_dict = {
                           'id_seqpos' : sample_data['id'].values[0] + '_' + str(i),
                           'reactivity_gt' : sample_data['reactivity'].values[0][i],
                           'deg_Mg_pH10_gt' : sample_data['deg_Mg_pH10'].values[0][i],
                           'deg_Mg_50C_gt' : sample_data['deg_Mg_50C'].values[0][i],
                           }
            val_data.append(sample_dict)
    val_data = pd.DataFrame(val_data)
    val_data = val_data.merge(prd, on='id_seqpos')

    rmses = []
    mses = []
    for col in ['reactivity', 'deg_Mg_pH10', 'deg_Mg_50C']:
        rmse = ((val_data[col] - val_data[col+'_gt']) ** 2).mean() ** .5
        mse = ((val_data[col] - val_data[col+'_gt']) ** 2).mean()
        rmses.append(rmse)
        mses.append(mse)
        print(col, rmse, mse)
    print(np.mean(rmses), np.mean(mses))

In [ ]:
print_mse(holdouts_df)

In [ ]:
print_mse(holdouts_df[holdouts_df.SN_filter == 1])